In [1]:
import pandas as pd
import numpy as np
import math
from scipy import spatial
from sklearn.metrics.pairwise import cosine_similarity

In [2]:
kp = pd.read_csv('/Users/caldavis/Documents/GitHub/Capstone-project/Data folder/KenPom Team Metrics.csv')
#kp.head(10)
kp_conf_rat = pd.read_csv('/Users/caldavis/Documents/GitHub/Capstone-project/Data folder/KP_Conf_Ratings.csv')
kp_conf_rat = kp_conf_rat[['Year_Conf', 'Conf_Abb', 'Conf_Rk', 'Conf_Full', 'Conf_Rating']]

d = pd.read_csv('/Users/caldavis/Documents/GitHub/Capstone-project/Data folder/final_data_by_player_type.csv')
d[d['Player.Name']=='babatunde-akingbola-1']


/var/folders/cq/16hkxgp926d466c0g9jzx2900000gq/T/ipykernel_34715/2295137300.py:6: DtypeWarning: Columns (13,16,38,144,147,169) have mixed types. Specify dtype option on import or set low_memory=False.
  d = pd.read_csv('/Users/caldavis/Documents/GitHub/Capstone-project/Data folder/final_data_by_player_type.csv')


Unnamed: 0  player_type    Team Team_n1  Unnamed..0_x  \
807         808            1  AUBURN  AUBURN       28111.0   

               Player.Name   season conf_abbr  games  games_started  ...  \
807  babatunde-akingbola-1  2019-20       SEC     13              0  ...   

     FTRate_n1  FTM.A_n1  Pct_n1 X2PM.A_n1  Pct.1_n1  X3PM.A_n1 Pct.2_n1  \
807       52.3      8-23   0.348     20-40       0.5        1-4     0.25   

     X.Pct_n1  X.2PM.A_n1 X.Pct.1_n1  
807     0.348       20-40        0.5  

[1 rows x 266 columns]

In [3]:
d = pd.merge(d, kp, left_on=['Team', 'year'], right_on=['TeamName', 'Season'], how='left')
d = pd.merge(d, kp, left_on=['Team_n1', 'year'], right_on=['TeamName', 'Season'], how='left')
df = pd.merge(d, kp, left_on=['Team_n1', 'year_n1'], right_on=['TeamName', 'Season'], how='left')
df = pd.merge(df, kp_conf_rat, left_on=['conf_abbr', 'year'], right_on=['Conf_Abb', 'Year_Conf'], how='left')
df = pd.merge(df, kp_conf_rat, left_on=['conf_abbr_n1', 'year'], right_on=['Conf_Abb', 'Year_Conf'], how='left')
df = pd.merge(df, kp_conf_rat, left_on=['conf_abbr_n1', 'year_n1'], right_on=['Conf_Abb', 'Year_Conf'], how='left')
df = df.replace(to_replace='NO IDEA', value=0)
df = df.replace(to_replace='---', value=0)
df = df.fillna(0)
df[df['Player.Name']=='demilade-adelekun-1']['year']

2674    0.0
Name: year, dtype: float64

In [4]:

df = df.drop(df.loc[((df['games']>39) & (df['year']==2023)) | ((df['games_n1']>39) & (df['year_n1']==2023)) | 
   ((df['games']>40) & (df['year']==2022)) | ((df['games_n1']>40) & (df['year_n1']==2022)) | 
   ((df['games']>33) & (df['year']==2021)) | ((df['games_n1']>33) & (df['year_n1']==2021)) | 
   ((df['games']>35) & (df['year']==2020)) | ((df['games_n1']>35) & (df['year_n1']==2020)) | 
   ((df['games']>40) & (df['year']==2019)) | ((df['games_n1']>40) & (df['year_n1']==2019))]['Player.Name'].index)

print(df[df['Player.Name']=='demilade-adelekun-1'])
# Add Year in School KP
year_cond = [(df['Yr_n1']=='Fr'), (df['Yr_n1']=='So'), 
             (df['Yr_n1']=='Jr'), (df['Yr_n1']=='Sr')]
year_val = [1, 2, 3, 4]
df['Class_n1'] = np.select(year_cond, year_val)
df['Year_dif'] = df['year_n1']-df['year']
df['Team_AdjEM_dif'] = df['AdjEM_y']-df['AdjEM_x']
df['KP_Rk_Dif'] = df['RankAdjEM_y']-df['RankAdjEM_x']
df['KP_Conf_Dif'] = df['Conf_Rating_y']-df['Conf_Rating_x']
df['Calc A'] = df['X.Min']*(df['ws']-min(df['ws']))
df['Calc A2'] = df['X.Min']*df['bpm']
# df['Calc A2'] = df['bpm']/(1-df['X.Min'])
df['Calc A3'] = df['X.Min']*df['ORtg']
df['Calc A2_n1'] = df['X.Min_n1']*df['bpm_n1']
# df['Calc A2_n1'] = df['bpm_n1']/(1-df['X.Min_n1'])
df['Calc A_n1'] =df['X.Min_n1']*(df['ws_n1']-min(df['ws_n1']))
df['Calc A3_n1'] = df['X.Min_n1']*df['ORtg_n1']
df['Calc B'] = (df['stl_per_poss']+df['blk_per_poss']+df['DR.'])*df['X.Min']
df['Calc B_n1'] = (df['stl_per_poss_n1']+df['blk_per_poss_n1']+df['DR._n1'])*df['X.Min_n1']
df['Calc C']=(df['off_rtg']-df['def_rtg'])*df['X.Min']
df['Calc C_n1']=(df['off_rtg_n1']-df['def_rtg_n1'])*df['X.Min_n1']
df['Calc Overall A'] = df['Calc A'] + df['Calc B']
df['Calc Overall A2'] = df['Calc A2'] + df['Calc B']
df['Calc Overall A3'] = df['Calc A3'] + df['Calc B']
df['Calc Overall A_n1'] = df['Calc A_n1'] + df['Calc B_n1']
df['Calc Overall A2_n1'] = df['Calc A2_n1'] + df['Calc B_n1']
df['Calc Overall A3_n1'] = df['Calc A3_n1'] + df['Calc B_n1']

df = df[['Player.Name', 'player_type', 'season_n1', 'Team_n1', 'conf_abbr_n1', 'Year_dif', 'Team_AdjEM_dif', 'Class_n1',
    'KP_Conf_Dif', 'Calc A_n1', 'Calc A2_n1', 'Calc A3_n1', 'Calc B_n1', 'Calc C_n1', 'Calc Overall A_n1', 'Calc Overall A2_n1', 'Calc Overall A3_n1']]
df[df['Player.Name']=='demilade-adelekun-1']


      Unnamed: 0  player_type       Team    Team_n1  Unnamed..0_x  \
2674        2675            1  DARTMOUTH  DARTMOUTH        8026.0   

              Player.Name   season conf_abbr  games  games_started  ...  \
2674  demilade-adelekun-1  2021-22       Ivy     20             11  ...   

      Year_Conf_y  Conf_Abb_y  Conf_Rk_y Conf_Full_y  Conf_Rating_y  \
2674          0.0           0        0.0           0            0.0   

      Year_Conf Conf_Abb  Conf_Rk  Conf_Full Conf_Rating  
2674        0.0        0      0.0          0         0.0  

[1 rows x 335 columns]


Player.Name  player_type season_n1    Team_n1 conf_abbr_n1  \
2674  demilade-adelekun-1            1   2022-23  DARTMOUTH          Ivy   

      Year_dif  Team_AdjEM_dif  Class_n1  KP_Conf_Dif  Calc A_n1  Calc A2_n1  \
2674       0.0             0.0         4          0.0     278.81      443.82   

      Calc A3_n1  Calc B_n1  Calc C_n1  Calc Overall A_n1  Calc Overall A2_n1  \
2674     6207.79    1769.59    1109.55             2048.4             2213.41   

      Calc Overall A3_n1  
2674             7977.38

In [5]:
br_pos = pd.read_excel("/Users/caldavis/Documents/GitHub/Capstone-project/Player ID MASTER (2018-19 - 2022-23).xlsx")
br_pos = br_pos[['PLAYER_ID', 'Season', 'Pos']]
br_pos[br_pos['PLAYER_ID']=='demilade-adelekun-1']

PLAYER_ID   Season Pos
2761   demilade-adelekun-1  2022-23   F
10246  demilade-adelekun-1  2021-22   F
19826  demilade-adelekun-1  2019-20   F

In [6]:
a = pd.read_csv("/Users/caldavis/Documents/GitHub/Capstone-project/Data folder/final_dataset.csv")
a = a[['Player Name', 'season', 'Team', 'conf_abbr', 'games', 'games_started', 'mp_per_g', 'fg_per_g', 'fga_per_g', 'fg_pct', 'fg2_per_g', 'fg2a_per_g', 'fg2_pct', 'fg3_per_g', 'fg3a_per_g', 'fg3_pct', 'ft_per_g', 'fta_per_g', 'ft_pct', 'orb_per_g', 'drb_per_g', 'trb_per_g', 'ast_per_g', 'stl_per_g', 'blk_per_g', 'tov_per_g', 'pf_per_g', 'pts_per_g', 'sos', 'mp', 'fg', 'fga', 'fg2', 'fg2a', 'fg2_pct.1', 'fg3', 'fg3a', 'ft', 'fta', 'orb', 'drb', 'trb', 'ast', 'stl', 'blk', 'tov', 'pf', 'pts', 'fg_per_min', 'fga_per_min', 'fg2_per_min', 'fg2a_per_min', 'fg3_per_min', 'fg3a_per_min', 'ft_per_min', 'fta_per_min', 'trb_per_min', 'ast_per_min', 'stl_per_min', 'blk_per_min', 'tov_per_min', 'pf_per_min', 'pts_per_min', 
    'fg_per_poss', 'fga_per_poss', 'fg2_per_poss', 'fg2a_per_poss', 'fg3_per_poss', 'fg3a_per_poss', 'ft_per_poss', 'fta_per_poss', 'trb_per_poss', 'ast_per_poss', 'stl_per_poss', 'blk_per_poss', 'tov_per_poss', 'pf_per_poss', 'pts_per_poss', 'off_rtg', 'def_rtg', 
    'per', 'ts_pct', 'efg_pct', 'fg3a_per_fga_pct', 'fta_per_fga_pct', 'pprod', 'orb_pct', 'drb_pct', 'trb_pct', 'ast_pct', 'stl_pct', 'blk_pct', 'tov_pct', 'usg_pct', 'ows', 'dws', 'ws', 'ws_per_40', 'obpm', 'dbpm', 'bpm', 'year', 'Ht', 'Wt', 
    'G', 'S', '%Min', 'ORtg', '%Poss', '%Shots']]
a[['games', 'games_started', 'mp_per_g', 'fg_per_g', 'fga_per_g', 'fg_pct', 'fg2_per_g', 'fg2a_per_g', 'fg2_pct', 'fg3_per_g', 'fg3a_per_g', 'fg3_pct', 'ft_per_g', 'fta_per_g', 'ft_pct', 'orb_per_g', 'drb_per_g', 'trb_per_g', 'ast_per_g', 'stl_per_g', 'blk_per_g', 'tov_per_g', 'pf_per_g', 'pts_per_g', 'sos', 'mp', 'fg', 'fga', 'fg2', 'fg2a', 'fg2_pct.1', 'fg3', 'fg3a', 'ft', 'fta', 'orb', 'drb', 'trb', 'ast', 'stl', 'blk', 'tov', 'pf', 'pts', 'fg_per_min', 'fga_per_min', 'fg2_per_min', 'fg2a_per_min', 'fg3_per_min', 'fg3a_per_min', 'ft_per_min', 'fta_per_min', 'trb_per_min', 'ast_per_min', 'stl_per_min', 'blk_per_min', 'tov_per_min', 'pf_per_min', 'pts_per_min', 
    'fg_per_poss', 'fga_per_poss', 'fg2_per_poss', 'fg2a_per_poss', 'fg3_per_poss', 'fg3a_per_poss', 'ft_per_poss', 'fta_per_poss', 'trb_per_poss', 'ast_per_poss', 'stl_per_poss', 'blk_per_poss', 'tov_per_poss', 'pf_per_poss', 'pts_per_poss', 'off_rtg', 'def_rtg', 
    'per', 'ts_pct', 'efg_pct', 'fg3a_per_fga_pct', 'fta_per_fga_pct', 'pprod', 'orb_pct', 'drb_pct', 'trb_pct', 'ast_pct', 'stl_pct', 'blk_pct', 'tov_pct', 'usg_pct', 'ows', 'dws', 'ws', 'ws_per_40', 'obpm', 'dbpm', 'bpm', 'year', 'Ht', 'Wt', 
    'G', 'S', '%Min', 'ORtg', '%Poss', '%Shots']].apply(pd.to_numeric, errors="ignore")
a = a.replace(to_replace='NO IDEA', value=0)
a = a.replace(to_replace='---', value=0)
a = a.fillna(0)
a = a.drop(a.loc[((a['games']>39) & (a['year']==2023)) | ((a['games']>40) & (a['year']==2022)) | 
   ((a['games']>33) & (a['year']==2021)) |  
   ((a['games']>35) & (a['year']==2020)) | 
   ((a['games']>40) & (a['year']==2019)) |
   (a['year']==0)]['Player Name'].index)
a[a['Player Name']=='demilade-adelekun-1']


/var/folders/cq/16hkxgp926d466c0g9jzx2900000gq/T/ipykernel_34715/4289016183.py:1: DtypeWarning: Columns (10,13,16,19,35) have mixed types. Specify dtype option on import or set low_memory=False.
  a = pd.read_csv("/Users/caldavis/Documents/GitHub/Capstone-project/Data folder/final_dataset.csv")


Player Name   season       Team conf_abbr  games  \
17716  demilade-adelekun-1  2021-22  DARTMOUTH       Ivy     20   
17717  demilade-adelekun-1  2022-23  DARTMOUTH       Ivy     27   

       games_started  mp_per_g  fg_per_g  fga_per_g fg_pct  ...  bpm  year  \
17716             11      18.1       3.0        5.0    0.5  ...  3.9  2022   
17717             27      23.3       5.6        9.9  0.833  ...  7.8  2023   

       Ht     Wt   G     S  %Min   ORtg %Poss  %Shots  
17716  80  220.0  20  11.0  37.2  119.8  23.8    19.2  
17717  80  220.0  25  25.0  56.9  109.1  31.0    30.2  

[2 rows x 110 columns]

In [7]:
df2 = pd.merge(df, br_pos, left_on=['Player.Name', 'season_n1'], right_on=['PLAYER_ID', 'Season'], how='left')
df2 = df2[['PLAYER_ID', 'Season', 'Pos', 'player_type', 'Team_n1', 'conf_abbr_n1',
       'Year_dif', 'Team_AdjEM_dif', 'Class_n1', 'KP_Conf_Dif', 'Calc A_n1',
       'Calc A2_n1', 'Calc A3_n1', 'Calc B_n1', 'Calc C_n1',
       'Calc Overall A_n1', 'Calc Overall A2_n1', 'Calc Overall A3_n1']]
df2[df2['PLAYER_ID']=='demilade-adelekun-1_2022']
#df.columns


Empty DataFrame
Columns: [PLAYER_ID, Season, Pos, player_type, Team_n1, conf_abbr_n1, Year_dif, Team_AdjEM_dif, Class_n1, KP_Conf_Dif, Calc A_n1, Calc A2_n1, Calc A3_n1, Calc B_n1, Calc C_n1, Calc Overall A_n1, Calc Overall A2_n1, Calc Overall A3_n1]
Index: []

In [8]:
df_final = pd.merge(df2, a, left_on=['PLAYER_ID', 'Season'], right_on=['Player Name', 'season'], how='inner')
pd.set_option('display.max_columns', None)

df_final['fg_pct']=df_final['fg_per_g']/df_final['fga_per_g']
df_final['fg2_pct']=df_final['fg2_per_g']/df_final['fg2a_per_g']
df_final['fg3_pct']=df_final['fg3_per_g']/df_final['fg3a_per_g']
df_final['ft_pct']=df_final['ft_per_g']/df_final['fta_per_g']

df_final = df_final.fillna(0)

# df_final['fg_pct']=df_final['fg_pct'].astype(str).astype(float)
# df_final['fg2_pct']=df_final['fg2_pct'].astype(str).astype(float)
# df_final['fg3_pct']=df_final['fg3_pct'].astype(str).astype(float)
# df_final['ft_pct']=df_final['ft_pct'].astype(str).astype(float)
df_final = df_final[(df_final['Season']=='2022-23') | (df_final['Season']=='2021-22')]
df_final = df_final[['PLAYER_ID', 'Season', 'Pos', 'player_type', 'Calc A2_n1', 'ORtg', 'KP_Conf_Dif', 'orb_pct', 
                     'Calc A3_n1', 'Calc B_n1', 'bpm', 'tov_pct', 'efg_pct', 'ws', 'Year_dif', 'fta_per_fga_pct', 
                     'fg3a_per_fga_pct', 'Ht', 'Wt', 'pts_per_g', 'fg_pct', 'fg2_pct', 'fg3_pct', 'ft_pct']]
# df_final = df_final[['PLAYER_ID', 'Season', 'Pos', 'player_type', 'trb_per_min', 'trb_per_poss', 'stl_per_poss', 'blk_per_poss', 'pf_per_poss', 
#  'off_rtg', 'def_rtg', 'per', 'efg_pct', 'fg3a_per_fga_pct', 'fta_per_fga_pct', 'pprod', 'orb_pct', 
#  'drb_pct', 'trb_pct', 'ast_pct', 'stl_pct', 'blk_pct', 'tov_pct', 'usg_pct', 'ows', 'dws', 'obpm', 
#  'dbpm', 'bpm', 'Ht', 'Wt', 'G', 'S', '%Min', 'ORtg', '%Poss', '%Shots', 
#    'Team_AdjEM_dif', 'KP_Conf_Dif', 'Calc A_n1', 'Calc A2_n1', 'Calc A3_n1', 'Calc B_n1', 'Calc C_n1', 'Calc Overall A_n1', 
#    'Calc Overall A2_n1', 'Calc Overall A3_n1','ws', 'Year_dif']]
df_final[df_final['PLAYER_ID']=='demilade-adelekun-1']

PLAYER_ID   Season Pos  player_type  Calc A2_n1   ORtg  \
2528  demilade-adelekun-1  2022-23   F            1      443.82  109.1   

      KP_Conf_Dif  orb_pct  Calc A3_n1  Calc B_n1  bpm  tov_pct  efg_pct   ws  \
2528          0.0     11.3     6207.79    1769.59  7.8     15.5    0.576  3.4   

      Year_dif  fta_per_fga_pct  fg3a_per_fga_pct  Ht     Wt  pts_per_g  \
2528       0.0            0.381             0.063  80  220.0       13.8   

        fg_pct   fg2_pct  fg3_pct    ft_pct  
2528  0.565657  0.569892      0.5  0.605263

In [9]:
# df3 = pd.read_csv("/Users/caldavis/Documents/GitHub/Capstone-project/Data folder/player_performances.csv")
# df3 = df3[['Player.Name', 'season', 'offensive_score', 'defensive_score']]
# df_final = pd.merge(df_final, df3, left_on=['PLAYER_ID', 'Season'], right_on=['Player.Name', 'season'], how='left')
# df_final = df_final.drop(['Player.Name', 'season'], axis=1)
# df_final

In [10]:
# df_simp = df[['fg_pct', 'fg2_pct', 'fg3_pct', 'ft_pct', 'fg_per_poss', 'fga_per_poss', 'fg2_per_poss', 'fg2a_per_poss', 'fg3_per_poss', 'fg3a_per_poss', 'ft_per_poss', 'fta_per_poss', 'trb_per_poss', 'ast_per_poss', 'stl_per_poss', 'blk_per_poss', 'tov_per_poss', 'pf_per_poss', 'pts_per_poss', 'off_rtg', 'def_rtg', 
#     'per', 'ts_pct', 'efg_pct', 'fg3a_per_fga_pct', 'fta_per_fga_pct', 'pprod', 'orb_pct', 'drb_pct', 'trb_pct', 'ast_pct', 'stl_pct', 'blk_pct', 'tov_pct', 'usg_pct', 'ows', 'dws', 'ws', 'ws_per_40', 'obpm', 'dbpm', 'bpm', 
#     'Ht', 'Wt', 'Conf_Rating', 'sos']]

df_simp = df_final[['Pos', 'player_type', 'Calc A2_n1', 'ORtg', 'KP_Conf_Dif', 'orb_pct', 'Calc A3_n1', 'Calc B_n1', 'bpm', 'tov_pct', 'efg_pct', 
                    'ws', 'Year_dif', 'fta_per_fga_pct', 'fg3a_per_fga_pct', 'Ht', 'Wt', 'pts_per_g', 'fg_pct', 'fg2_pct', 'fg3_pct', 'ft_pct']]
# df_simp = df_final[['Pos', 'player_type', 'trb_per_min', 'trb_per_poss', 'stl_per_poss', 'blk_per_poss', 'pf_per_poss', 
#     'off_rtg', 'def_rtg', 'per', 'efg_pct', 'fg3a_per_fga_pct', 'fta_per_fga_pct', 'pprod', 'orb_pct', 
#  'drb_pct', 'trb_pct', 'ast_pct', 'stl_pct', 'blk_pct', 'tov_pct', 'usg_pct', 'ows', 'dws', 'obpm', 
#  'dbpm', 'bpm', 'Ht', 'Wt', 'G', 'S', '%Min', 'ORtg', '%Poss', '%Shots', 
#    'Team_AdjEM_dif', 'KP_Conf_Dif', 'Calc A_n1', 'Calc A2_n1', 'Calc A3_n1', 'Calc B_n1', 'Calc C_n1', 'Calc Overall A_n1', 
#    'Calc Overall A2_n1', 'Calc Overall A3_n1','ws', 'Year_dif']]
#df_simp = list(set(df_simp))



In [11]:
len(df_simp.columns)

22

In [12]:
df_std_g = df_simp[df_simp['Pos']=='G']
df_std_g = df_std_g.drop(['Pos'], axis=1)
df_std_g = (df_std_g-df_std_g.mean())/df_std_g.std()
print(len(df_std_g.columns))
df_name = df_final[['PLAYER_ID', 'Season', 'Pos']]
df_name['year'] = df_name['Season'].str[-2:].astype(int)+2000
df_name['Player_Year'] = df_name['PLAYER_ID'] + "_" + df_name['year'].astype(int).astype(str)
df_std_g = pd.merge(df_name, df_std_g, left_index=True, right_index=True)
df_std_g = df_std_g.drop(['PLAYER_ID', 'year', 'Season', 'Pos'], axis=1)

df_g_p = df_std_g
df_g_p = df_g_p[df_g_p['player_type']<0]
df_g_col_p = list(df_g_p['Player_Year'])
df_g_p = df_g_p.set_index('Player_Year')

df_g = df_std_g
df_g_col = list(df_g['Player_Year']) # List of player-seasons
df_g = df_g.set_index('Player_Year') # Setting index to player-season


21


/var/folders/cq/16hkxgp926d466c0g9jzx2900000gq/T/ipykernel_34715/3624214232.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_name['year'] = df_name['Season'].str[-2:].astype(int)+2000
/var/folders/cq/16hkxgp926d466c0g9jzx2900000gq/T/ipykernel_34715/3624214232.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_name['Player_Year'] = df_name['PLAYER_ID'] + "_" + df_name['year'].astype(int).astype(str)


In [13]:

df_g_cs = cosine_similarity(df_g, df_g)
df_g_cs = pd.DataFrame(df_g_cs, columns=df_g_col)
columns=df_g_col_p
df_g_cs['Player'] = df_g_col
df_g_cs = df_g_cs.set_index('Player')
df_g_cs

aanen-moody-1_2022  aanen-moody-1_2023  \
Player                                                         
aanen-moody-1_2022              1.000000            0.480598   
aanen-moody-1_2023              0.480598            1.000000   
aaron-cash-1_2023              -0.143493            0.113252   
aaron-clarke-1_2022             0.313526            0.372060   
aaron-clarke-1_2023            -0.357927           -0.271323   
...                                  ...                 ...   
zion-russell-1_2023            -0.542182           -0.766438   
zion-williams-2_2022           -0.518380           -0.064874   
zion-young-1_2022               0.362746           -0.170320   
zyon-pullin-1_2022              0.062727            0.527478   
zyon-pullin-1_2023              0.209046            0.658813   

                      aaron-cash-1_2023  aaron-clarke-1_2022  \
Player                                                         
aanen-moody-1_2022            -0.143493             0.313526   
aanen-moody-1_2023             0.113252             0.372060   
aaron-cash-1_2023              1.000000            -0.368151   
aaron-clarke-1_2022           -0.368151             1.000000   
aaron-clarke-1_2023           -0.404106             0.012653   
...                                 ...                  ...   
zion-russell-1_2023           -0.111946            -0.232222   
zion-williams-2_2022           0.708429            -0.365626   
zion-young-1_2022             -0.075282             0.114624   
zyon-pullin-1_2022            -0.100447             0.250745   
zyon-pullin-1_2023            -0.092088             0.335414   

                      aaron-clarke-1_2023  aaron-cook-2_2022  \
Player                                                         
aanen-moody-1_2022              -0.357927          -0.452986   
aanen-moody-1_2023              -0.271323           0.043372   
aaron-cash-1_2023               -0.404106          -0.270772   
aaron-clarke-1_2022              0.012653           0.112223   
aaron-clarke-1_2023              1.000000           0.614022   
...                                   ...                ...   
zion-russell-1_2023              0.528263           0.166260   
zion-williams-2_2022            -0.239723           0.114777   
zion-young-1_2022               -0.017949          -0.244885   
zyon-pullin-1_2022              -0.534799          -0.084922   
zyon-pullin-1_2023              -0.476710          -0.198943   

                      aaron-cooley-1_2023  aaron-deloney-1_2022  \
Player                                                            
aanen-moody-1_2022              -0.385360              0.788502   
aanen-moody-1_2023              -0.658969              0.379953   
aaron-cash-1_2023               -0.060382             -0.222731   
aaron-clarke-1_2022             -0.285925              0.330817   
aaron-clarke-1_2023             -0.104352             -0.316916   
...                                   ...                   ...   
zion-russell-1_2023              0.383947             -0.254298   
zion-williams-2_2022             0.183426             -0.358882   
zion-young-1_2022               -0.002421              0.337209   
zyon-pullin-1_2022              -0.058876              0.093885   
zyon-pullin-1_2023              -0.222089              0.310022   

                      aaron-deloney-1_2023  aaron-duhart-1_2022  \
Player                                                            
aanen-moody-1_2022                0.725704             0.050415   
aanen-moody-1_2023                0.612248            -0.141991   
aaron-cash-1_2023                -0.275238            -0.283181   
aaron-clarke-1_2022               0.464518             0.530470   
aaron-clarke-1_2023              -0.330538             0.064283   
...                                    ...                  ...   
zion-russell-1_2023              -0.403021             0.198950   
zion-williams-2_2022             -0.425325      

In [14]:
#trey-phipps-1_2021-22
df_g_cs['max-shulga-1_2023'].sort_values(ascending=False).head(15)

Player
max-shulga-1_2023           1.000000
lucas-williamson-1_2022     0.957888
tyler-kolek-1_2023          0.948580
jaden-ivey-1_2022           0.943457
vince-williams-2_2022       0.936532
trey-alexander-1_2023       0.936131
kobe-bufkin-1_2023          0.928036
andrew-nembhard-1_2022      0.927424
collin-gillespie-1_2022     0.927358
tristen-newton-1_2022       0.922460
baylor-scheierman-1_2022    0.922286
isaiah-wong-1_2023          0.919973
jamaree-bouyea-1_2022       0.918476
tevin-brown-1_2022          0.917404
ochai-agbaji-1_2022         0.916979
Name: max-shulga-1_2023, dtype: float64

In [15]:
#df_g_cs['max-abmas-1_2023']['tylor-perry-1_2023']

In [16]:
df_g_cs['jason-nelson-1_2023'].sort_values(ascending=False).head(15)

KeyError: 'jason-nelson-1_2023'

In [17]:
df_std_f = df_simp[df_simp['Pos']=='F']
df_std_f = df_std_f.drop(['Pos'], axis=1)
df_std_f = (df_std_f-df_std_f.mean())/df_std_f.std()

df_name = df_final[['PLAYER_ID', 'Season', 'Pos']]
df_name['year'] = df_name['Season'].str[-2:].astype(int)+2000
df_name['Player_Year'] = df_name['PLAYER_ID'] + "_" + df_name['year'].astype(int).astype(str)
df_std_f = pd.merge(df_name, df_std_f, left_index=True, right_index=True)
df_std_f = df_std_f.drop(['PLAYER_ID', 'year', 'Season', 'Pos'], axis=1)


df_f = df_std_f
df_f_col = list(df_f['Player_Year']) # List of player-seasons
df_f = df_f.set_index('Player_Year') # Setting index to player-season

df_f_cs = cosine_similarity(df_f, df_f)
df_f_cs= pd.DataFrame(df_f_cs, columns=df_f_col)
df_f_cs['Player'] = df_f_col
df_f_cs = df_f_cs.set_index('Player')
df_f_cs

/var/folders/cq/16hkxgp926d466c0g9jzx2900000gq/T/ipykernel_34715/440778840.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_name['year'] = df_name['Season'].str[-2:].astype(int)+2000
/var/folders/cq/16hkxgp926d466c0g9jzx2900000gq/T/ipykernel_34715/440778840.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_name['Player_Year'] = df_name['PLAYER_ID'] + "_" + df_name['year'].astype(int).astype(str)


aaron-murphy-1_2022  aaron-reddish-1_2023  \
Player                                                             
aaron-murphy-1_2022               1.000000             -0.058531   
aaron-reddish-1_2023             -0.058531              1.000000   
aaron-wheeler-2_2022             -0.779962             -0.129687   
abayomi-iyiola-1_2022            -0.023454             -0.570278   
abayomi-iyiola-1_2023             0.110462             -0.195121   
...                                    ...                   ...   
zion-griffin-1_2022              -0.091479              0.247489   
zion-griffin-1_2023              -0.293187              0.243833   
zion-tordoff-1_2022               0.371514              0.010602   
zoar-nedd-1_2022                  0.142686              0.572897   
zoar-nedd-1_2023                  0.414436             -0.114514   

                       aaron-wheeler-2_2022  abayomi-iyiola-1_2022  \
Player                                                               
aaron-murphy-1_2022               -0.779962              -0.023454   
aaron-reddish-1_2023              -0.129687              -0.570278   
aaron-wheeler-2_2022               1.000000               0.230987   
abayomi-iyiola-1_2022              0.230987               1.000000   
abayomi-iyiola-1_2023             -0.178041               0.320723   
...                                     ...                    ...   
zion-griffin-1_2022                0.200748               0.148715   
zion-griffin-1_2023                0.444864               0.056967   
zion-tordoff-1_2022               -0.171265               0.393337   
zoar-nedd-1_2022                  -0.204186              -0.563597   
zoar-nedd-1_2023                  -0.332366              -0.389952   

                       abayomi-iyiola-1_2023  abdou-ndiaye-1_2022  \
Player                                                              
aaron-murphy-1_2022                 0.110462             0.525842   
aaron-reddish-1_2023               -0.195121            -0.234738   
aaron-wheeler-2_2022               -0.178041            -0.418923   
abayomi-iyiola-1_2022               0.320723            -0.055973   
abayomi-iyiola-1_2023               1.000000             0.201615   
...                                      ...                  ...   
zion-griffin-1_2022                -0.383358            -0.329645   
zion-griffin-1_2023                -0.051757            -0.444561   
zion-tordoff-1_2022                 0.228907            -0.047405   
zoar-nedd-1_2022                   -0.122191             0.210067   
zoar-nedd-1_2023                   -0.197986             0.660941   

                       abdou-tsimbila-1_2022  abdou-tsimbila-1_2023  \
Player                                                                
aaron-murphy-1_2022                 0.356772               0.286781   
aaron-reddish-1_2023               -0.366098              -0.430583   
aaron-wheeler-2_2022               -0.261000              -0.511805   
abayomi-iyiola-1_2022               0.195814               0.230263   
abayomi-iyiola-1_2023              -0.011078               0.176829   
...                                      ...                    ...   
zion-griffin-1_2022                -0.570721              -0.489307   
zion-griffin-1_2023                -0.232854              -0.548548   
zion-tordoff-1_2022                 0.387174               0.040877   
zoar-nedd-1_2022                   -0.007882              -0.210314   
zoar-nedd-1_2023                    0.264008              -0.009683   

                       abdul-momoh-1_2023  abe-johnson-1_2023  \
Player                                                          
aaron-murphy-1_2022              0.836131            0.647421   
aaron-reddish-1_2023             0.030764           -0.590750   
aaron-wheeler-2_2022            -0.743974           -0.418186   
abayomi-iyiola-1_2022           -0.059918            0.432437   
abayomi-iyiola-

In [18]:
df_f_cs['patrick-mwamba-1_2023'].sort_values(ascending=False).head(15)

Player
patrick-mwamba-1_2023       1.000000
zion-griffin-1_2023         0.821852
angelo-allegri-1_2022       0.818585
devin-tillis-1_2023         0.816534
tyrone-lyons-1_2022         0.794466
joe-pleasant-1_2023         0.791478
melik-martin-1_2022         0.775445
trey-anderson-2_2022        0.762770
cam-burrell-1_2023          0.759982
judah-brown-1_2023          0.749353
jaylen-sebree-1_2023        0.742706
emmitt-matthewsjr-1_2022    0.741157
jerome-desrosiers-1_2022    0.738860
mikey-henn-1_2022           0.733120
malek-green-1_2023          0.732230
Name: patrick-mwamba-1_2023, dtype: float64

In [19]:
df_std_c = df_simp[df_simp['Pos']=='C']
df_std_c = df_std_c.drop(['Pos'], axis=1)
df_std_c = (df_std_c-df_std_c.mean())/df_std_c.std()

df_name = df_final[['PLAYER_ID', 'Season', 'Pos']]
df_name['year'] = df_name['Season'].str[-2:].astype(int)+2000
df_name['Player_Year'] = df_name['PLAYER_ID'] + "_" + df_name['year'].astype(int).astype(str)
df_std_c = pd.merge(df_name, df_std_c, left_index=True, right_index=True)
df_std_c = df_std_c.drop(['PLAYER_ID', 'year', 'Season', 'Pos'], axis=1)

df_c = df_std_c
df_c_col = list(df_c['Player_Year']) # List of player-seasons
df_c = df_c.set_index('Player_Year') # Setting index to player-season

df_c_cs = cosine_similarity(df_c, df_c)
df_c_cs= pd.DataFrame(df_c_cs, columns=df_c_col)
df_c_cs['Player'] = df_c_col
df_c_cs = df_c_cs.set_index('Player')
df_c_cs

/var/folders/cq/16hkxgp926d466c0g9jzx2900000gq/T/ipykernel_34715/2904334942.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_name['year'] = df_name['Season'].str[-2:].astype(int)+2000
/var/folders/cq/16hkxgp926d466c0g9jzx2900000gq/T/ipykernel_34715/2904334942.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_name['Player_Year'] = df_name['PLAYER_ID'] + "_" + df_name['year'].astype(int).astype(str)


abba-lawal-1_2022  adam-cisse-1_2023  \
Player                                                         
abba-lawal-1_2022                1.000000           0.221354   
adam-cisse-1_2023                0.221354           1.000000   
ahsan-asadullah-1_2022          -0.347606          -0.239548   
ahsan-asadullah-1_2023           0.211595          -0.139600   
aj-braun-1_2023                 -0.502165           0.092031   
...                                   ...                ...   
zach-iyeyemi-1_2023              0.196138           0.273820   
zach-riley-1_2023                0.031672           0.391064   
zach-visentin-1_2022             0.719965           0.255825   
zeke-richards-1_2022             0.042730           0.109466   
zeke-richards-1_2023             0.153041           0.125800   

                        ahsan-asadullah-1_2022  ahsan-asadullah-1_2023  \
Player                                                                   
abba-lawal-1_2022                    -0.347606                0.211595   
adam-cisse-1_2023                    -0.239548               -0.139600   
ahsan-asadullah-1_2022                1.000000                0.367208   
ahsan-asadullah-1_2023                0.367208                1.000000   
aj-braun-1_2023                       0.332968                0.125654   
...                                        ...                     ...   
zach-iyeyemi-1_2023                  -0.283397                0.120365   
zach-riley-1_2023                     0.232527                0.016337   
zach-visentin-1_2022                 -0.213571                0.316522   
zeke-richards-1_2022                 -0.071053               -0.068289   
zeke-richards-1_2023                 -0.209202               -0.214451   

                        aj-braun-1_2023  alex-christie-1_2022  \
Player                                                          
abba-lawal-1_2022             -0.502165              0.383533   
adam-cisse-1_2023              0.092031              0.081645   
ahsan-asadullah-1_2022         0.332968             -0.399037   
ahsan-asadullah-1_2023         0.125654              0.138877   
aj-braun-1_2023                1.000000             -0.467611   
...                                 ...                   ...   
zach-iyeyemi-1_2023            0.132539              0.507345   
zach-riley-1_2023             -0.047122              0.038606   
zach-visentin-1_2022          -0.301629              0.643103   
zeke-richards-1_2022           0.074589             -0.031258   
zeke-richards-1_2023          -0.176536              0.555740   

                        alex-tew-1_2023  alex-timmerman-1_2022  \
Player                                                           
abba-lawal-1_2022             -0.159781              -0.353818   
adam-cisse-1_2023              0.015654              -0.086635   
ahsan-asadullah-1_2022         0.148275               0.597363   
ahsan-asadullah-1_2023         0.506876               0.122250   
aj-braun-1_2023                0.616263               0.373991   
...                                 ...                    ...   
zach-iyeyemi-1_2023            0.144434               0.266005   
zach-riley-1_2023             -0.367386               0.303621   
zach-visentin-1_2022          -0.089020               0.079784   
zeke-richards-1_2022          -0.050519               0.118291   
zeke-richards-1_2023          -0.230596               0.244822   

                        alex-timmerman-1_2023  amari-mccray-1_2022  \
Player                                                               
abba-lawal-1_2022                   -0.403104             0.056186   
adam-cisse-1_2023                   -0.071096            -0.157983   
ahsan-asadullah-1_2022               0.829427             0.053099   
ahsan-asadullah-1_2023               0.281059             0.031206   
aj-braun-1_2023                      0.502990            -0.156091   
...                              

In [20]:
df_c_cs['andre-screen-1_2023'].sort_values(ascending=False).head(15)

Player
andre-screen-1_2023        1.000000
russel-tchewa-1_2023       0.830214
callum-mcrae-1_2022        0.816984
andre-screen-1_2022        0.794005
oumar-ballo-1_2023         0.688020
clifford-omoruyi-1_2022    0.685337
trey-jemison-1_2022        0.684341
jason-spurgin-1_2023       0.644485
kofi-cockburn-1_2022       0.625068
alex-tew-1_2023            0.591999
roman-silva-1_2022         0.590824
trey-jemison-1_2023        0.588177
jacob-germany-1_2022       0.576628
braxton-meah-1_2023        0.574923
callum-mcrae-1_2023        0.574075
Name: andre-screen-1_2023, dtype: float64

In [21]:
df_g_cs.to_csv('/Users/caldavis/Desktop/Guard Matrix.csv', index=True)
df_f_cs.to_csv('/Users/caldavis/Desktop/Forward Matrix.csv', index=True)
df_c_cs.to_csv('/Users/caldavis/Desktop/Center Matrix.csv', index=True)

KeyboardInterrupt: 

In [ ]:
def magnitude(v, cols):
  word = (math.sqrt(sum(v[n].iloc[0]*v[n].iloc[0] for n in cols)))
  return word

def cosine(v1, v2, cols):
  dot_product = sum([v1[i].iloc[0]*v2[i].iloc[0] for i in cols])
  return(dot_product/(magnitude(v1, cols)*magnitude(v2, cols)))

#print(cosine(c, d, c.columns))
#matrix = pd.DataFrame()


In [ ]:
#df_std = df_std.drop(['Pos'], axis=1)

In [ ]:

a_list = ['zach-edey-1_2022', 'zach-edey-1_2023', 'hunter-dickinson-1_2022', 'hunter-dickinson-1_2023', 
          'jake-stephens-1_2022', 'tre-mitchell-1_2022', 'tre-mitchell-1_2023']

b_list = list(df_std['Player_Year'].unique())
#print(type(a_list))
matrix = {'id1': [], 'id2': [], 'Similarity': []}
for id1 in a_list:
  print(id1)
  #print(id1, type(id1), )
  for id2 in b_list:
    if id1 == id2: continue
    v1 = df_std[df_std['Player_Year']==id1]
    v1 = v1.drop('Player_Year', axis=1)
    v2 = df_std[df_std['Player_Year']==id2]
    v2 = v2.drop('Player_Year', axis=1)
    matrix['id1'].append(id1)
    matrix['id2'].append(id2)
    #print(v1.columns)
    matrix['Similarity'].append(cosine(v1,v2, list(v1.columns)))
    #v1.columns
    #= matrix{'id1':id1, 'id2':id2, 'similarity':cosine(v1,v2, v1.columns)}]))

sim_matrix = pd.DataFrame(matrix, columns=['id1', 'id2', 'Similarity'])

sim_matrix


#matrix

NameError: name 'df_std' is not defined

In [ ]:
sim_matrix[sim_matrix['id1']=='zach-edey-1_2022'].sort_values('Similarity', ascending=False).head(5)

id1                     id2  Similarity
176   zach-edey-1_2022    kofi-cockburn-1_2022    0.962017
7     zach-edey-1_2022        zach-edey-1_2023    0.957756
770   zach-edey-1_2022  colin-castleton-1_2022    0.951927
6692  zach-edey-1_2022       tolu-smith-1_2023    0.940547
6797  zach-edey-1_2022      nfaly-dante-1_2023    0.937940

In [ ]:
from scipy import spatial
# a_list = list(df_c['Player_Year'].unique())
# b_list = a_list
a_list = ['zach-edey-1_2022', 'zach-edey-1_2023', 'hunter-dickinson-1_2022', 'hunter-dickinson-1_2023']
 #         'jake-stephens-1_2022', 'tre-mitchell-1_2022', 'tre-mitchell-1_2023']

b_list = list(df_c['Player_Year'].unique())
#print(type(a_list))
matrix = {'id1': [], 'id2': [], 'Similarity': []}
for id1 in a_list:
  print(id1)
  #print(id1, type(id1), )
  for id2 in b_list:
    if id1 == id2: continue
    v1 = df_c[df_c['Player_Year']==id1]
    v1 = v1.drop('Player_Year', axis=1)
    v2 = df_c[df_c['Player_Year']==id2]
    v2 = v2.drop('Player_Year', axis=1)
    matrix['id1'].append(id1)
    matrix['id2'].append(id2)
    #matrix['Similarity'].append(1-spatial.distance.cosine(v1.iloc[0], v2.iloc[0]))
    #v1.columns
    #= matrix{'id1':id1, 'id2':id2, 'similarity':cosine(v1,v2, v1.columns)}]))

sim_matrix_c = pd.DataFrame(matrix, columns=['id1', 'id2', 'Similarity'])

sim_matrix_c

In [ ]:
#df_c = df_std[df_std['Pos']=='C']
#df_c = df_c.drop(['Pos'], axis=1)
df_c_col = list(df_c['Player_Year'])
df_c = df_c.set_index('Player_Year')

In [ ]:
df2

zach-edey-1_2022  zach-edey-1_2023  \
Temp                                                          
zach-edey-1_2022                 1.000000          0.957756   
zach-edey-1_2023                 0.957756          1.000000   
hunter-dickinson-1_2022          0.899990          0.924135   
hunter-dickinson-1_2023          0.886203          0.939474   
jake-stephens-1_2022             0.794896          0.837739   
...                                   ...               ...   
zeke-richards-1_2023             0.123550          0.015092   
grant-asman-1_2022               0.104875          0.056397   
grant-asman-1_2023               0.220446          0.202789   
ludgy-debaut-1_2022              0.052619          0.059795   
ludgy-debaut-1_2023              0.118861          0.076729   

                         hunter-dickinson-1_2022  hunter-dickinson-1_2023  \
Temp                                                                        
zach-edey-1_2022                        0.899990                 0.886203   
zach-edey-1_2023                        0.924135                 0.939474   
hunter-dickinson-1_2022                 1.000000                 0.966640   
hunter-dickinson-1_2023                 0.966640                 1.000000   
jake-stephens-1_2022                    0.869014                 0.852399   
...                                          ...                      ...   
zeke-richards-1_2023                   -0.017442                -0.082503   
grant-asman-1_2022                     -0.018206                -0.008826   
grant-asman-1_2023                      0.249488                 0.272840   
ludgy-debaut-1_2022                     0.051091                 0.062861   
ludgy-debaut-1_2023                    -0.054319                -0.028166   

                         jake-stephens-1_2022  jake-stephens-1_2023  \
Temp                                                                  
zach-edey-1_2022                     0.794896              0.864522   
zach-edey-1_2023                     0.837739              0.862509   
hunter-dickinson-1_2022              0.869014              0.858247   
hunter-dickinson-1_2023              0.852399              0.843356   
jake-stephens-1_2022                 1.000000              0.959781   
...                                       ...                   ...   
zeke-richards-1_2023                -0.126838             -0.108709   
grant-asman-1_2022                   0.075670              0.236686   
grant-asman-1_2023                   0.348952              0.385291   
ludgy-debaut-1_2022                 -0.055413             -0.096344   
ludgy-debaut-1_2023                 -0.165039             -0.149682   

                         kofi-cockburn-1_2022  ahsan-asadullah-1_2022  \
Temp                                                                    
zach-edey-1_2022                     0.962017                0.766709   
zach-edey-1_2023                     0.946686                0.700554   
hunter-dickinson-1_2022              0.887623                0.717715   
hunter-dickinson-1_2023              0.894001                0.658615   
jake-stephens-1_2022                 0.742450                0.666091   
...                                       ...                     ...   
zeke-richards-1_2023                 0.074866                0.018004   
grant-asman-1_2022                   0.013929                0.297101   
grant-asman-1_2023                   0.062333                0.296422   
ludgy-debaut-1_2022                 -0.034269               -0.074283   
ludgy-debaut-1_2023                  0.050852               -0.096809   

                         ahsan-asadullah-1_2023  morris-udeze-1_2022  ...  \
Temp                                                                  ...   
zach-edey-1_2022                       0.383357             0.825052  ...   
zach-edey-1_2023                       0.336843             0.767564  ...   
hunter-dickinson-1_20

In [ ]:
df2['zach-edey-1_2022'].sort_values(ascending=False).head()

Temp
zach-edey-1_2022        1.000000
kofi-cockburn-1_2022    0.962017
zach-edey-1_2023        0.957756
nfaly-dante-1_2023      0.937940
oumar-ballo-1_2023      0.908891
Name: zach-edey-1_2022, dtype: float64

In [ ]:
#sim_matrix_c.to_csv("Similarity_Matrix_Centers.csv")

In [ ]:
sim_matrix_c[sim_matrix_c['id1']=='zach-edey-1_2023'].sort_values('Similarity', ascending=False).head(5)

#sim_matrix_c[sim_matrix_c['id1']=='hunter-dickinson-1_2022'].sort_values('Similarity', ascending=False).head(5)

#sim_matrix_c[sim_matrix_c['id1']=='zeke-richards-1_2022'].sort_values('Similarity', ascending=False).head(5)

id1                      id2  Similarity
305  zach-edey-1_2023         zach-edey-1_2022    0.956708
310  zach-edey-1_2023     kofi-cockburn-1_2022    0.944014
307  zach-edey-1_2023  hunter-dickinson-1_2023    0.939045
593  zach-edey-1_2023       oumar-ballo-1_2023    0.935382
314  zach-edey-1_2023      morris-udeze-1_2023    0.928507

In [ ]:
from scipy import spatial
df_f = df_f.sort_values('Player_Year')
a_list = list(df_f['Player_Year'].unique())
b_list = a_list

#print(type(a_list))
matrix = {'id1': [], 'id2': [], 'Similarity': []}
for id1 in a_list:
  print(id1)
  #print(id1, type(id1), )
  for id2 in b_list:
    if id1 == id2: continue
    v1 = df_f[df_f['Player_Year']==id1]
    v1 = v1.drop('Player_Year', axis=1)
    v2 = df_f[df_f['Player_Year']==id2]
    v2 = v2.drop('Player_Year', axis=1)
    matrix['id1'].append(id1)
    matrix['id2'].append(id2)
    matrix['Similarity'].append(1-spatial.distance.cosine(v1.iloc[0], v2.iloc[0]))
    #v1.columns
    #= matrix{'id1':id1, 'id2':id2, 'similarity':cosine(v1,v2, v1.columns)}]))

sim_matrix_f = pd.DataFrame(matrix, columns=['id1', 'id2', 'Similarity'])

sim_matrix_f

aaron-murphy-1_2022
aaron-reddish-1_2022
aaron-reddish-1_2023
aaron-wheeler-2_2022
abayomi-iyiola-1_2022
abayomi-iyiola-1_2023
abdou-ndiaye-1_2022
abdou-samb-1_2023
abdou-tsimbila-1_2022
abdou-tsimbila-1_2023
abdul-ado-1_2022
abdul-momoh-1_2023
abe-johnson-1_2023
abou-ousmane-1_2022
abou-ousmane-1_2023
abu-kigab-1_2022
adam-larson-1_2023
adam-thistlewood-1_2022
adama-sanogo-1_2022
adama-sanogo-1_2023
adem-bona-1_2023
ademide-badmus-1_2023
aguek-arop-1_2022
aguek-arop-1_2023
ahjany-lee-1_2023
ahmard-harvey-1_2023
ahmir-langlais-1_2022
ahmir-langlais-1_2023
aidan-igiehon-1_2022
aidan-igiehon-1_2023
aidan-shaw-1_2023
airion-simmons-1_2022
airion-simmons-1_2023
aj-allenspach-1_2022
aj-casey-1_2023
aj-clayton-1_2022
aj-clayton-1_2023
aj-edu-1_2023
aj-george-1_2023
aj-griffin-1_2022
aj-taylor-1_2022
aj-wilson-2_2022
ajang-aguek-1_2022
ajiri-johnson-1_2022
ajiri-johnson-1_2023
akeem-odusipe-1_2022
akok-akok-1_2022
akok-akok-1_2023
akol-arop-1_2022
akol-arop-1_2023
alanzo-frink-1_2022
alden-ap

id1                    id2  Similarity
0          aaron-murphy-1_2022   aaron-reddish-1_2022    0.225010
1          aaron-murphy-1_2022   aaron-reddish-1_2023    0.006931
2          aaron-murphy-1_2022   aaron-wheeler-2_2022   -0.292554
3          aaron-murphy-1_2022  abayomi-iyiola-1_2022    0.485996
4          aaron-murphy-1_2022  abayomi-iyiola-1_2023    0.575343
...                        ...                    ...         ...
5815327  zurabi-zhgenti-1_2022     zinou-bedri-1_2023    0.640234
5815328  zurabi-zhgenti-1_2022    zion-griffin-1_2022   -0.273897
5815329  zurabi-zhgenti-1_2022    zion-griffin-1_2023    0.059453
5815330  zurabi-zhgenti-1_2022    zion-tordoff-1_2022    0.449062
5815331  zurabi-zhgenti-1_2022       zoar-nedd-1_2022    0.244474

[5815332 rows x 3 columns]

In [ ]:
sim_matrix_f.to_csv("Similarity_Matrix_Forwards.csv")

In [ ]:
#sim_matrix_f[sim_matrix_f['id1']=='drew-timme-1_2022'].sort_values('Similarity', ascending=False).head(5)

sim_matrix_f[sim_matrix_f['id1']=='keegan-murray-1_2022'].sort_values('Similarity', ascending=False).head(5)

sim_matrix_f[sim_matrix_f['id1']=='keve-aluma-1_2022'].sort_values('Similarity', ascending=False).head(5)

id1                      id2  Similarity
3339254  keve-aluma-1_2022      adama-sanogo-1_2023    0.980305
3339406  keve-aluma-1_2022   azuolas-tubelis-1_2023    0.972410
3341115  keve-aluma-1_2022    paolo-banchero-1_2022    0.961324
3339801  keve-aluma-1_2022  deandre-williams-1_2023    0.960356
3339890  keve-aluma-1_2022        drew-timme-1_2023    0.960145

In [ ]:
from scipy import spatial
df_g = df_g.sort_values('Player_Year')
a_list = list(df_g['Player_Year'].unique())
b_list = a_list

#print(type(a_list))
matrix = {'id1': [], 'id2': [], 'Similarity': []}
for id1 in a_list:
  print(id1)
  #print(id1, type(id1), )
  for id2 in b_list:
    if id1 == id2: continue
    v1 = df_g[df_g['Player_Year']==id1]
    v1 = v1.drop('Player_Year', axis=1)
    v2 = df_g[df_g['Player_Year']==id2]
    v2 = v2.drop('Player_Year', axis=1)
    matrix['id1'].append(id1)
    matrix['id2'].append(id2)
    matrix['Similarity'].append(1-spatial.distance.cosine(v1.iloc[0], v2.iloc[0]))
    #v1.columns
    #= matrix{'id1':id1, 'id2':id2, 'similarity':cosine(v1,v2, v1.columns)}]))

sim_matrix_g = pd.DataFrame(matrix, columns=['id1', 'id2', 'Similarity'])

sim_matrix_g

aamer-muhammad-1_2023
aanen-moody-1_2022
aanen-moody-1_2023
aaron-cash-1_2022
aaron-cash-1_2023
aaron-clarke-1_2022
aaron-cook-2_2022
aaron-cooley-1_2022
aaron-cooley-1_2023
aaron-deloney-1_2022
aaron-deloney-1_2023
aaron-duhart-1_2022
aaron-estrada-1_2022
aaron-estrada-1_2023
aaron-gray-2_2023
aaron-lemon-warren-1_2023
aaron-scott-5_2022
aaron-scott-5_2023
aaron-thompson-3_2022
aaryn-rai-1_2022
abdoulaye-thiam-1_2023
abdul-mohamed-1_2022
aboubacar-traore-1_2022
aboubacar-traore-1_2023
ac-curry-1_2023
achile-spadone-1_2023
adam-flagler-1_2022
adam-flagler-1_2023
adam-hess-2_2023
adam-kunkel-1_2022
adam-kunkel-1_2023
adam-miller-3_2023
adam-seiko-1_2022
adam-seiko-1_2023
adam-silas-1_2023
adama-bal-1_2023
adante-holiman-1_2023
ade-adebayo-1_2022
ade-adebayo-1_2023
adefolalrin-adetogun-1_2022
adefolalrin-adetogun-1_2023
adetokunbo-bakare-1_2023
adham-eleeda-1_2022
adonis-arms-1_2022
adou-thiero-1_2023
adrian-balwinjr-1_2022
adrian-balwinjr-1_2023
adrian-delph-1_2022
adrian-martin-2_2022


id1                   id2  Similarity
0           aamer-muhammad-1_2023    aanen-moody-1_2022    0.320461
1           aamer-muhammad-1_2023    aanen-moody-1_2023    0.518100
2           aamer-muhammad-1_2023     aaron-cash-1_2022   -0.698760
3           aamer-muhammad-1_2023     aaron-cash-1_2023    0.013353
4           aamer-muhammad-1_2023   aaron-clarke-1_2022    0.561260
...                           ...                   ...         ...
16986757  zytarious-mortle-1_2023   zion-russell-1_2022    0.339291
16986758  zytarious-mortle-1_2023    zion-styles-1_2023    0.600846
16986759  zytarious-mortle-1_2023  zion-williams-2_2022    0.456867
16986760  zytarious-mortle-1_2023    zyon-pullin-1_2022   -0.074825
16986761  zytarious-mortle-1_2023    zyon-pullin-1_2023   -0.041926

[16986762 rows x 3 columns]

In [ ]:
sim_matrix_g.to_csv("Similarity_Matrix_Guards.csv")

In [ ]:
#sim_matrix['True'] = 1-sim_matrix['Similarity']
sim_matrix = pd.concat([sim_matrix_c, sim_matrix_f, sim_matrix_g])
sim_matrix

id1                      id2  Similarity
0                zach-edey-1_2022         zach-edey-1_2023    0.956708
1                zach-edey-1_2022  hunter-dickinson-1_2022    0.900140
2                zach-edey-1_2022  hunter-dickinson-1_2023    0.885337
3                zach-edey-1_2022     jake-stephens-1_2022    0.795056
4                zach-edey-1_2022     jake-stephens-1_2023    0.863639
...                           ...                      ...         ...
16986757  zytarious-mortle-1_2023      zion-russell-1_2022    0.339291
16986758  zytarious-mortle-1_2023       zion-styles-1_2023    0.600846
16986759  zytarious-mortle-1_2023     zion-williams-2_2022    0.456867
16986760  zytarious-mortle-1_2023       zyon-pullin-1_2022   -0.074825
16986761  zytarious-mortle-1_2023       zyon-pullin-1_2023   -0.041926

[22895424 rows x 3 columns]

In [ ]:
sim_matrix.to_csv("Full_Similarity_Matrix.csv")

In [ ]:
sim_matrix[sim_matrix['id1']=='james-bishop-2_2020'].sort_values('Similarity', ascending=False).head(5)

sim_matrix[sim_matrix['id1']=='brendan-adams-1_2022'].sort_values('Similarity', ascending=False).head(5)

sim_matrix[sim_matrix['id1']=='keegan-murray-1_2022'].sort_values('Similarity', ascending=False).head(5)

id1                      id2  Similarity
151  keegan-murray-1_2022       david-roddy-1_2022    0.953149
211  keegan-murray-1_2022        keve-aluma-1_2022    0.951684
116  keegan-murray-1_2022       kj-williams-1_2023    0.949189
173  keegan-murray-1_2022       kris-murray-1_2023    0.948218
107  keegan-murray-1_2022  deandre-williams-1_2023    0.921589

In [ ]:
# from scipy import spatial
# a_list = list(df_std['Player_Year'].unique())
# a_list = a_list[4800:5300]
# #print(type(a_list))
# matrix = {'id1': [], 'id2': [], 'Similarity': []}
# for id1 in a_list:
#   print(id1)
#   #print(id1, type(id1), )
#   for id2 in a_list:
#     if id1 == id2: continue
#     v1 = df_std[df_std['Player_Year']==id1]
#     v1 = v1.drop('Player_Year', axis=1)
#     v2 = df_std[df_std['Player_Year']==id2]
#     v2 = v2.drop('Player_Year', axis=1)
#     matrix['id1'].append(id1)
#     matrix['id2'].append(id2)
#     matrix['Similarity'].append(1-spatial.distance.cosine(v1.iloc[0], v2.iloc[0]))
#     #v1.columns
#     #= matrix{'id1':id1, 'id2':id2, 'similarity':cosine(v1,v2, v1.columns)}]))

# sim_matrix2 = pd.DataFrame(matrix, columns=['id1', 'id2', 'Similarity'])

# sim_matrix2

In [ ]:
# a = list(df_std['Player_Year'].unique())
# a = a[0:4800]
# a[4799]

'kamani-johnson-1_2022'